# BVM library examples: single-dataset for all combinations of QIDs

In [1]:
import pandas
from bvmlib.bvm import BVM

In [2]:
import os
import multiprocessing
from itertools import chain, combinations
import tqdm
tqdm.tqdm.monitor_interval = 0

def powerset(iterable):
    "powerset([1,2,3]) --> () (1,) (2,) (3,) (1,2) (1,3) (2,3) (1,2,3)"
    s = list(iterable)
    return chain.from_iterable(combinations(s, r) for r in range(len(s)+1))

## INEP School Census for 2018

In [3]:
def load():
    source = '/home/nunesgh/temp/inep-school-2018.csv'
    df = pandas.read_csv(source, low_memory=False)
    return df

In [4]:
df = load()
display(df)

NU_DIA  NU_MES  NU_ANO  TP_SEXO  TP_COR_RACA  TP_NACIONALIDADE  \
0             28      11    2006        2            1                 1   
1              7       7    2015        1            3                 1   
2             17       7    2015        1            0                 1   
3             25       1    2006        1            1                 1   
4             22       4    2007        1            3                 1   
...          ...     ...     ...      ...          ...               ...   
48176418      13       6    2003        2            3                 1   
48176419       5       8    2008        2            1                 1   
48176420      12       8    2012        2            3                 1   
48176421       2       2    2004        1            1                 1   
48176422      17       7    2013        1            0                 1   

          CO_PAIS_ORIGEM  CO_MUNICIPIO_NASC  CO_MUNICIPIO_END  \
0                     76            2112407           2112407   
1                     76            3170404           3116159   
2                     76            3148103           3148103   
3                     76            2611606           2611606   
4                     76            1501303           1501303   
...                  ...                ...               ...   
48176418              76            5003702           5003504   
48176419              76            3550308                -1   
48176420              76            3521804                -1   
48176421              76            3550308                -1   
48176422              76            3550308                -1   

          IN_TRANSPORTE_PUBLICO  IN_NECESSIDADE_ESPECIAL  CO_ENTIDADE  \
0                             0                        0     21069131   
1                             0                        0     31337056   
2                             0                        0     31200212   
3                             0                        0     26122162   
4                             1                        0     15036774   
...                         ...                      ...          ...   
48176418                      0                        0     50015591   
48176419                      0                        0     35813000   
48176420                      1                        0     35498973   
48176421                      0                        0     35103548   
48176422                      0                        0     35298244   

          TP_DEPENDENCIA  
0                      3  
1                      3  
2                      4  
3                      4  
4                      3  
...                  ...  
48176418               2  
48176419               4  
48176420               3  
48176421               4  
48176422               3  

[48176423 rows x 13 columns]

Description of selected attributes.
- 'NU_DIA': day of birth
- 'NU_MES': month of birth
- 'NU_ANO': year of birth
- 'TP_SEXO': gender
- 'TP_COR_RACA': ethnicity
- 'TP_NACIONALIDADE': nationality
- 'CO_PAIS_ORIGEM': country of birth
- 'CO_MUNICIPIO_NASC': city of birth
- 'CO_MUNICIPIO_END': city of residency
- 'CO_ENTIDADE': school id code
- 'TP_DEPENDENCIA': school type
- 'IN_NECESSIDADE_ESPECIAL': disability status
- 'IN_TRANSPORTE_PUBLICO': public school transportation

In [5]:
data1 = None
data2 = None

def init(_data1,_data2):
    global data1
    data1 = _data1
    global data2
    data2 = _data2

pool_size = multiprocessing.cpu_count() * 1

os.system('taskset -cp 0-%d %s' % (pool_size, os.getpid()))

quasi_identifiers = ['NU_DIA','NU_MES','NU_ANO','TP_SEXO','TP_COR_RACA','TP_NACIONALIDADE','CO_PAIS_ORIGEM',
                     'CO_MUNICIPIO_NASC','CO_MUNICIPIO_END','CO_ENTIDADE','TP_DEPENDENCIA']
sensitive_attributes = ['IN_NECESSIDADE_ESPECIAL','IN_TRANSPORTE_PUBLICO']

def job(quasi_identifiers):
    inep18 = BVM(df)
    inep18.qids(list(quasi_identifiers))
    inep18.sensitive(sensitive_attributes)
    return inep18.assess()

with multiprocessing.Pool(processes=pool_size, maxtasksperchild=1, initializer=init,
                          initargs=(df, sensitive_attributes)) as P:
    pool_outputs = list(tqdm.tqdm(P.imap(job, powerset(quasi_identifiers)),
                                  total=sum(1 for _ in powerset(quasi_identifiers))))

P.close()
P.join()

pid 40261's current affinity list: 0-39
pid 40261's new affinity list: 0-39


100%|██████████| 2048/2048 [8:53:29<00:00, 15.63s/it]   


In [6]:
inep18 ={}
inep18['re_id'] = pool_outputs[1]['re_id']
inep18['att_inf'] = pool_outputs[1]['att_inf']
for subset in range(2, 2**len(quasi_identifiers)):
    inep18['re_id'] = pandas.concat([inep18['re_id'], pool_outputs[subset]['re_id']], ignore_index=True)
    inep18['att_inf'] = pandas.concat([inep18['att_inf'], pool_outputs[subset]['att_inf']], ignore_index=True)

In [7]:
with pandas.option_context('display.max_rows', None, 'display.max_columns', None):
    display(inep18['re_id'].set_index('QID'))
    display(inep18['att_inf'].set_index(['QID', 'Sensitive']))

dCR       pCR Prior  \
QID                                                                            
['NU_DIA']                                               0.0        31   0.0   
['NU_MES']                                               0.0        12   0.0   
['NU_ANO']                                               0.0       107   0.0   
['TP_SEXO']                                              0.0         2   0.0   
['TP_COR_RACA']                                          0.0         6   0.0   
['TP_NACIONALIDADE']                                     0.0         3   0.0   
['CO_PAIS_ORIGEM']                                       0.0       203   0.0   
['CO_MUNICIPIO_NASC']                                    0.0      5571   0.0   
['CO_MUNICIPIO_END']                                     0.0      5564   0.0   
['CO_ENTIDADE']                                     0.000002    183706   0.0   
['TP_DEPENDENCIA']                                       0.0         4   0.0   
['NU_DIA', 'NU_MES']                                     0.0       366   0.0   
['NU_DIA', 'NU_ANO']                                0.000002      3083   0.0   
['NU_DIA', 'TP_SEXO']                                    0.0        62   0.0   
['NU_DIA', 'TP_COR_RACA']                                0.0       186   0.0   
['NU_DIA', 'TP_NACIONALIDADE']                           0.0        93   0.0   
['NU_DIA', 'CO_PAIS_ORIGEM']                        0.000021      3057   0.0   
['NU_DIA', 'CO_MUNICIPIO_NASC']                     0.000167    165485   0.0   
['NU_DIA', 'CO_MUNICIPIO_END']                      0.000062    166129   0.0   
['NU_DIA', 'CO_ENTIDADE']                           0.013871   5000106   0.0   
['NU_DIA', 'TP_DEPENDENCIA']                             0.0       124   0.0   
['NU_MES', 'NU_ANO']                                0.000001      1220   0.0   
['NU_MES', 'TP_SEXO']                                    0.0        24   0.0   
['NU_MES', 'TP_COR_RACA']                                0.0        72   0.0   
['NU_MES', 'TP_NACIONALIDADE']                           0.0        36   0.0   
['NU_MES', 'CO_PAIS_ORIGEM']                        0.000008      1544   0.0   
['NU_MES', 'CO_MUNICIPIO_NASC']                     0.000024     66027   0.0   
['NU_MES', 'CO_MUNICIPIO_END']                      0.000021     65373   0.0   
['NU_MES', 'CO_ENTIDADE']                           0.002557   2115337   0.0   
['NU_MES', 'TP_DEPENDENCIA']                             0.0        48   0.0   
['NU_ANO', 'TP_SEXO']                                    0.0       213   0.0   
['NU_ANO', 'TP_COR_RACA']                                0.0       610   0.0   
['NU_ANO', 'TP_NACIONALIDADE']                           0.0       273   0.0   
['NU_ANO', 'CO_PAIS_ORIGEM']                        0.000025      3231   0.0   
['NU_ANO', 'CO_MUNICIPIO_NASC']                      0.00119    312856   0.0   
['NU_ANO', 'CO_MUNICIPIO_END']                      0.001001    292200   0.0   
['NU_ANO', 'CO_ENTIDADE']                           0.012742   2645719   0.0   
['NU_ANO', 'TP_DEPENDENCIA']                             0.0       396   0.0   
['TP_SEXO', 'TP_COR_RACA']                               0.0        12   0.0   
['TP_SEXO', 'TP_NACIONALIDADE']                          0.0         6   0.0   
['TP_SEXO', 'CO_PAIS_ORIGEM']                       0.000001       367   0.0   
['TP_SEXO', 'CO_MUNICIPIO_NASC']                         0.0     11141   0.0   
['TP_SEXO', 'CO_MUNICIPIO_END']                     0.000001     11095   0.0   
['TP_SEXO', 'CO_ENTIDADE']                          0.000022    366724   0.0   
['TP_SEXO', 'TP_DEPENDENCIA']                            0.0         8   0.0   
['TP_COR_RACA', 'TP_NACIONALIDADE']                      0.0        18   0.0   
['TP_COR_RACA', 'CO_PAIS_ORIGEM']                   0.000003       654   0.0   
['TP_COR_RACA', 'CO_MUNICIPIO_NASC']                0.000039     29023   0.0   
['TP_COR_RACA', 'CO_MUNICIPIO_END']                 0.000

dCA  \
QID                                                Sensitive                           
['NU_DIA']                                         IN_NECESSIDADE_ESPECIAL       0.0   
                                                   IN_TRANSPORTE_PUBLICO         0.0   
['NU_MES']                                         IN_NECESSIDADE_ESPECIAL       0.0   
                                                   IN_TRANSPORTE_PUBLICO         0.0   
['NU_ANO']                                         IN_NECESSIDADE_ESPECIAL  0.000001   
                                                   IN_TRANSPORTE_PUBLICO         0.0   
['TP_SEXO']                                        IN_NECESSIDADE_ESPECIAL       0.0   
                                                   IN_TRANSPORTE_PUBLICO         0.0   
['TP_COR_RACA']                                    IN_NECESSIDADE_ESPECIAL       0.0   
                                                   IN_TRANSPORTE_PUBLICO         0.0   
['TP_NACIONALIDADE']                               IN_NECESSIDADE_ESPECIAL       0.0   
                                                   IN_TRANSPORTE_PUBLICO         0.0   
['CO_PAIS_ORIGEM']                                 IN_NECESSIDADE_ESPECIAL   0.00006   
                                                   IN_TRANSPORTE_PUBLICO    0.000019   
['CO_MUNICIPIO_NASC']                              IN_NECESSIDADE_ESPECIAL  0.000219   
                                                   IN_TRANSPORTE_PUBLICO    0.000004   
['CO_MUNICIPIO_END']                               IN_NECESSIDADE_ESPECIAL  0.000151   
                                                   IN_TRANSPORTE_PUBLICO     0.00002   
['CO_ENTIDADE']                                    IN_NECESSIDADE_ESPECIAL  0.123097   
                                                   IN_TRANSPORTE_PUBLICO    0.420818   
['TP_DEPENDENCIA']                                 IN_NECESSIDADE_ESPECIAL       0.0   
                                                   IN_TRANSPORTE_PUBLICO         0.0   
['NU_DIA', 'NU_MES']                               IN_NECESSIDADE_ESPECIAL       0.0   
                                                   IN_TRANSPORTE_PUBLICO         0.0   
['NU_DIA', 'NU_ANO']                               IN_NECESSIDADE_ESPECIAL  0.000142   
                                                   IN_TRANSPORTE_PUBLICO    0.000017   
['NU_DIA', 'TP_SEXO']                              IN_NECESSIDADE_ESPECIAL       0.0   
                                                   IN_TRANSPORTE_PUBLICO         0.0   
['NU_DIA', 'TP_COR_RACA']                          IN_NECESSIDADE_ESPECIAL       0.0   
                                                   IN_TRANSPORTE_PUBLICO         0.0   
['NU_DIA', 'TP_NACIONALIDADE']                     IN_NECESSIDADE_ESPECIAL       0.0   
                                                   IN_TRANSPORTE_PUBLICO         0.0   
['NU_DIA', 'CO_PAIS_ORIGEM']                       IN_NECESSIDADE_ESPECIAL  0.000426   
                                                   IN_TRANSPORTE_PUBLICO    0.000171   
['NU_DIA', 'CO_MUNICIPIO_NASC']                    IN_NECESSIDADE_ESPECIAL  0.021815   
                                                   IN_TRANSPORTE_PUBLICO    0.001148   
['NU_DIA', 'CO_MUNICIPIO_END']                     IN_NECESSIDADE_ESPECIAL  0.031323   
                                                   IN_TRANSPORTE_PUBLICO     0.00059   
['NU_DIA', 'CO_ENTIDADE']                          IN_NECESSIDADE_ESPECIAL  0.710376   
                                                   IN_TRANSPORTE_PUBLICO    0.600196   
['NU_DIA', 'TP_DEPENDENCIA']                       IN_NECESSIDADE_ESPECIAL       0.0   
                                                   IN_TRANSPORTE_PUBLICO         0.0   
['NU_MES', 'NU_ANO']                               IN_NECESSIDADE_ESPECIAL  0.000035   
                                                   IN_TRANSPORTE_PUBLICO    0.000006   
['NU_MES', 'TP_SEXO']            

---